# Homework 3 

You will have 2 datasets to work on. 
#### You have to answer questions in this [form](https://goo.gl/forms/5gfxvKZxpoydoeOB2) and provide your code

### 1. Wikipedia Web Traffic Time Series

Data from [Kaggle competition](https://www.kaggle.com/c/web-traffic-time-series-forecasting)* )

*wikipedia_train3* - train data *wikipedia_test3* - test data created by us from original train data . For more information about dataset, please visit Homework1 assignment


### 2. French dataset

Target variable is prime_tot_ttc – house of insurance price.<p>
The variables in the files are:<p>
code_postal: postal code of the insured property<p>
nb_pieces: number of rooms<p>
veranda: presence of a veranda<p>
biens_nomades: ceiling of coverage of goods (laptop, tablets, musical instruments ,…)<p>
sit_fam: family situation of the insured<p>
profession: profession of the insured<p>
nature_lri: nature of the insured property<p>
societe: company covering the risk<p>
cdomact: area of activity of the insured<p>
niv_urbanisation: level of urbanization in which is the insured property<p>
age_societaire: age of the member<p>
objets_precieux: presence of precious objects in the insured property<p>
pres_contrat_auto: holding a contract of auto insurance<p>
formule: guarantee formula<p>
sit_juridique: legal situation<p>
surf_habitat: area of insured property<p>
patrimoine_mob: amount of heritage insured furniture<p>
var1 - ... - var11: non-explicit variables<p>


## Wikipedia page views (SMAPE metric)

In [2]:
import pandas as pd
import numpy as np

In [65]:
### This is data from wikipedia3 archive in data folder

train = pd.read_csv("../data/wikipedia_train3.csv")
test = pd.read_csv("../data/wikipedia_test3.csv")

In [66]:
def pandas_smape(df):
    df.fillna(0, inplace=True)
    df["SMAPE"] = 200 * np.abs(df["Visits"] - df["pred_Visits"]) / (df["Visits"] + df["pred_Visits"])
    df["SMAPE"].fillna(0, inplace=True)
    return np.mean(df["SMAPE"])

**1.** Take a look carefuly at train and test dataset. Note for you what is the difference in them and how they are dependent. **For _only_ train** create a holdout validation using any type of split you think is useful here. What is the split type you are using? Answer in google forms

**2.** Write a code to compare the score of your validation and test set. For scoring, use metric SMAPE (code is in lecture). For prediction use 15 previous days median. In the google form write your validation score.

In [37]:
import pandas_profiling as pp

In [7]:
pp.ProfileReport(train)


In [8]:
pp.ProfileReport(test)


In [76]:
from dateutil.relativedelta import relativedelta

def holdout_split(df,split_date,delta_days):
    train = df.loc[pd.to_datetime(df['date']) <= pd.to_datetime(split_date)]
    validate = df.loc[pd.to_datetime(df['date']) >= pd.to_datetime(split_date) + relativedelta(days = delta_days)]
    return train,validate

In [98]:

split_date = pd.to_datetime(train.date.max())-relativedelta(days = 72)
delta_days = 10

t,v = holdout_split(train,split_date,delta_days)

In [99]:
median_starting_date = split_date - relativedelta(days = 15)

t_median = t.loc[pd.to_datetime(t["date"]) > median_starting_date].groupby(['Page']).median().reset_index()
t_median.rename(columns={"Visits": "pred_Visits"}, inplace=True)

In [100]:
answer = v.merge(t_median, on="Page", how='left')
pandas_smape(answer)

45.183691767816278

In [ ]:
import math 

def smape_fast(y_true, y_pred):
    out = 0
    for i in range(y_true.shape[0]):
        a = y_true[i]
        b = y_pred[i]
        if b < 1:
            b = 0
        c = a+b
        if c == 0:
            continue
        out += math.fabs(a - b) / c
    out *= (200.0 / y_true.shape[0])
    return out

In [103]:
'''

y_t = answer.Visits.values
y_p = answer.pred_Visits.values

smape_fast(y_t,y_p)
'''

45.183691767820228

In [96]:
# PREDICT FOR TEST SET
split_date = train.date.max()
median_starting_date = pd.to_datetime(split_date)-relativedelta(days = 15)

train_median = train.loc[pd.to_datetime(train["date"]) > median_starting_date].groupby(['Page']).median().reset_index()
train_median.rename(columns={"Visits": "pred_Visits"}, inplace=True)

answer_test = test.merge(train_median, on="Page", how='left')
pandas_smape(answer_test)

40.007012702044264

**3.** Perform K-fold validation using your type of split. Run GridSearch with any classificator you like and set of parameters to optimize, providing it with your custom validation.  Compare the score of your validation and test set. For scoring, again, use metrics SMAPE. In the google form write your scores on validation and test sets

In [4]:
def create_validation(df, start_date, delta_days = 10, train_days = 117, validate_days = 31):
    end_date_train = pd.to_datetime(start_date)+relativedelta(days = train_days)
    train = df.loc[(pd.to_datetime(df['date']) >= pd.to_datetime(start_date)) & (pd.to_datetime(df['date']) <= end_date_train)]
    
    end_date_test = end_date_train + relativedelta(days = delta_days + validate_days)
    validate = df.loc[(pd.to_datetime(df['date']) >= (end_date_train + relativedelta(days = delta_days))) & (pd.to_datetime(df['date']) <= end_date_test)]
    
    return train.index, validate.index

In [7]:
train_dates = [pd.to_datetime(train.date.min()), pd.to_datetime(train.date.min()) + relativedelta(days = 29), pd.to_datetime(train.date.min()) + relativedelta(days = 57), pd.to_datetime(train.date.min()) + relativedelta(days = 86)]
train_dates

[Timestamp('2016-01-01 00:00:00'),
 Timestamp('2016-01-30 00:00:00'),
 Timestamp('2016-02-27 00:00:00'),
 Timestamp('2016-03-27 00:00:00')]

In [8]:
myCViterator = []
for i in train_dates:
    trainIndices, valIndices = create_validation(train, i)
    myCViterator.append( (trainIndices, valIndices) )

In [10]:
#encoded = pd.get_dummies(train, columns = ['Page'])
train['Page'] = train['Page'].astype('category')

In [12]:
train['Page_cat'] = train['Page'].cat.codes


In [18]:
everything = pd.concat([train,test])
everything.sample(5)

Page        date  \
205523       Mexico_en.wikipedia.org_all-access_all-agents  2016-01-18   
554938         東山奈央_ja.wikipedia.org_all-access_all-agents  2016-02-16   
1908046  Alexander_Skarsgård_en.wikipedia.org_all-acces...  2016-06-10   
1117244   Australia_en.wikipedia.org_mobile-web_all-agents  2016-04-04   
859756   Antigua_Grecia_es.wikipedia.org_all-access_all...  2016-03-13   

          Visits  
205523   11007.0  
554938    2871.0  
1908046   7825.0  
1117244   8434.0  
859756    3212.0

In [19]:
everything['Page'] = everything['Page'].astype('category')
everything['Page_cat'] = everything['Page'].cat.codes

In [22]:
everything['date'] = pd.to_datetime(everything['date'])

In [27]:
everything['weekday'] = everything['date'].dt.dayofweek

In [34]:
everything['day'] = everything['date'].dt.day
everything['month'] = everything['date'].dt.month

In [35]:
everything.sample(5)

Page       date  Visits  \
327221   Philippines_en.wikipedia.org_mobile-web_all-ag... 2016-01-28  5846.0   
614164   Mats_Hummels_de.wikipedia.org_all-access_all-a... 2016-10-31   276.0   
1699608  Zinedine_Zidane_es.wikipedia.org_mobile-web_al... 2016-05-23  1233.0   
2770589  Special:Search_de.wikipedia.org_all-access_spider 2016-08-22   906.0   
1713433   Dean_Ambrose_en.wikipedia.org_desktop_all-agents 2016-05-25  2402.0   

         Page_cat  weekday  day  month  
327221       6937        3   28      1  
614164       5862        0   31     10  
1699608     10019        0   23      5  
2770589      8188        0   22      8  
1713433      2219        2   25      5

In [2]:
everything.sample(5)

In [107]:
train_1 = everything[everything['month'] < 9]
test_1 = everything[everything['month'] > 9]

y_train = train_1['Visits']
y_test = test_1['Visits']

X_train_1 = train_1.drop(['Page','date','Visits'],axis = 1)
X_test_1 = test_1.drop(['Page','date','Visits'],axis = 1)

In [112]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV


regressor = xgb.XGBRegressor(seed = 42, objective = 'reg:linear')

pipeline_r = Pipeline([('regressor', regressor)])
param_grid = {'regressor__max_depth':[5,8],'regressor__learning_rate': [0.05, 0.1], 'regressor__subsample': [0.7,0.9],'regressor__colsample_bytree': [0.7,0.8], 'regressor__reg_lambda': [0.7]}
grid_search = GridSearchCV(pipeline_r, param_grid=param_grid, cv=myCViterator,scoring = 'neg_mean_absolute_error',verbose = 3, n_jobs = 3)


In [113]:
grid_search.fit(X_train_1,y_train)


Fitting 4 folds for each of 16 candidates, totalling 64 fits
[CV] regressor__learning_rate=0.05, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=5, regressor__reg_lambda=0.7 
[CV] regressor__learning_rate=0.05, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=5, regressor__reg_lambda=0.7 
[CV] regressor__learning_rate=0.05, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=5, regressor__reg_lambda=0.7 
[CV]  regressor__learning_rate=0.05, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=5, regressor__reg_lambda=0.7, score=-6824.790793, total=  58.2s
[CV] regressor__learning_rate=0.05, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=5, regressor__reg_lambda=0.7 
[CV]  regressor__learning_rate=0.05, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=5, regressor__reg_lambda=0.7, score=-11133.367214, total=

[CV] regressor__learning_rate=0.1, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=8, regressor__reg_lambda=0.7 
[CV]  regressor__learning_rate=0.1, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=8, regressor__reg_lambda=0.7, score=-5282.643178, total= 1.5min
[CV] regressor__learning_rate=0.1, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=8, regressor__reg_lambda=0.7 
[CV]  regressor__learning_rate=0.1, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=8, regressor__reg_lambda=0.7, score=-5386.700904, total= 1.5min
[CV] regressor__learning_rate=0.1, regressor__colsample_bytree=0.7, regressor__subsample=0.9, regressor__max_depth=8, regressor__reg_lambda=0.7 


[Parallel(n_jobs=3)]: Done  26 tasks      | elapsed: 11.6min


[CV]  regressor__learning_rate=0.1, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=8, regressor__reg_lambda=0.7, score=-9720.746675, total= 1.5min
[CV] regressor__learning_rate=0.1, regressor__colsample_bytree=0.7, regressor__subsample=0.9, regressor__max_depth=8, regressor__reg_lambda=0.7 
[CV]  regressor__learning_rate=0.1, regressor__colsample_bytree=0.7, regressor__subsample=0.7, regressor__max_depth=8, regressor__reg_lambda=0.7, score=-10052.409686, total= 1.5min
[CV] regressor__learning_rate=0.1, regressor__colsample_bytree=0.7, regressor__subsample=0.9, regressor__max_depth=8, regressor__reg_lambda=0.7 
[CV]  regressor__learning_rate=0.1, regressor__colsample_bytree=0.7, regressor__subsample=0.9, regressor__max_depth=8, regressor__reg_lambda=0.7, score=-5303.226298, total= 1.4min
[CV] regressor__learning_rate=0.1, regressor__colsample_bytree=0.7, regressor__subsample=0.9, regressor__max_depth=8, regressor__reg_lambda=0.7 
[CV]  regressor__learnin

[CV] regressor__learning_rate=0.1, regressor__colsample_bytree=0.8, regressor__subsample=0.9, regressor__max_depth=5, regressor__reg_lambda=0.7 
[CV]  regressor__learning_rate=0.1, regressor__colsample_bytree=0.8, regressor__subsample=0.9, regressor__max_depth=5, regressor__reg_lambda=0.7, score=-5951.369533, total=  54.1s
[CV] regressor__learning_rate=0.1, regressor__colsample_bytree=0.8, regressor__subsample=0.9, regressor__max_depth=5, regressor__reg_lambda=0.7 
[CV]  regressor__learning_rate=0.1, regressor__colsample_bytree=0.8, regressor__subsample=0.9, regressor__max_depth=5, regressor__reg_lambda=0.7, score=-6114.768739, total=  53.3s
[CV] regressor__learning_rate=0.1, regressor__colsample_bytree=0.8, regressor__subsample=0.7, regressor__max_depth=8, regressor__reg_lambda=0.7 
[CV]  regressor__learning_rate=0.1, regressor__colsample_bytree=0.8, regressor__subsample=0.9, regressor__max_depth=5, regressor__reg_lambda=0.7, score=-10268.805001, total=  53.2s
[CV] regressor__learning

[Parallel(n_jobs=3)]: Done  64 out of  64 | elapsed: 29.4min finished


GridSearchCV(cv=[(Int64Index([      0,       1,       2,       3,       4,       5,       6,
                  7,       8,       9,
            ...
            1394160, 1394161, 1394162, 1394163, 1394164, 1394165, 1394166,
            1394167, 1394168, 1394169],
           dtype='int64', length=1394170), Int64In...2882855, 2882856,
            2882857, 2882858, 2882859],
           dtype='int64', length=366265))],
       error_score='raise',
       estimator=Pipeline(steps=[('regressor', XGBRegressor(base_score=0.5, colsample_bylevel=1, colsample_bytree=1, gamma=0,
       learning_rate=0.1, max_delta_step=0, max_depth=3,
       min_child_weight=1, missing=None, n_estimators=100, nthread=-1,
       objective='reg:linear', reg_alpha=0, reg_lambda=1,
       scale_pos_weight=1, seed=42, silent=True, subsample=1))]),
       fit_params={}, iid=True, n_jobs=3,
       param_grid={'regressor__learning_rate': [0.05, 0.1], 'regressor__max_depth': [5, 8], 'regressor__subsample': [0.7, 0.9], 'regre

In [114]:
grid_search.best_params_

{'regressor__colsample_bytree': 0.7,
 'regressor__learning_rate': 0.1,
 'regressor__max_depth': 8,
 'regressor__reg_lambda': 0.7,
 'regressor__subsample': 0.7}

In [126]:
res = []
for i in range(4):

    X_tr = X_train_1.iloc[myCViterator[i][0]]
    y_tr = y_train.iloc[myCViterator[i][0]]
    
    X_te = X_train_1.iloc[myCViterator[i][1]]
    y_te = y_train.iloc[myCViterator[i][1]]

    xgb_train = xgb.DMatrix(X_tr, label=y_tr)
    xgb_val = xgb.DMatrix(X_te, label=y_te)
    
    params = {
    'eta': 0.1, 
    'seed': 42, 
    'subsample': 0.7, 
    'colsample_bytree': 0.7,
    'objective': 'reg:linear', 
    'reg_lambda':0.7,
    'max_depth': 8, 
    'eval_metric': 'mae' 
    }

    eval_matrix = [(xgb_val, 'xgb_val')]

    final_gb = xgb.train(params, xgb_train, evals = eval_matrix,verbose_eval=1)
    
    dtest = xgb.DMatrix(X_te)
    y_xgb_2 = final_gb.predict(dtest)

    res.append(smape_fast(y_te.values,y_xgb_2))
    

[0]	xgb_val-mae:9674.27
[1]	xgb_val-mae:8846.32
[2]	xgb_val-mae:8178.69
[3]	xgb_val-mae:7781.81
[4]	xgb_val-mae:7673.11
[5]	xgb_val-mae:7737.11
[6]	xgb_val-mae:7896.19
[7]	xgb_val-mae:7655.18
[8]	xgb_val-mae:7416.96
[9]	xgb_val-mae:7210.22
[0]	xgb_val-mae:10050.2
[1]	xgb_val-mae:9230.88
[2]	xgb_val-mae:8573.6
[3]	xgb_val-mae:8217.58
[4]	xgb_val-mae:8114.33
[5]	xgb_val-mae:8175.98
[6]	xgb_val-mae:8320.12
[7]	xgb_val-mae:8073.51
[8]	xgb_val-mae:7868.62
[9]	xgb_val-mae:7668.5
[0]	xgb_val-mae:13904.1
[1]	xgb_val-mae:13126.3
[2]	xgb_val-mae:12491.4
[3]	xgb_val-mae:12160.3
[4]	xgb_val-mae:12090
[5]	xgb_val-mae:12179.7
[6]	xgb_val-mae:12348.2
[7]	xgb_val-mae:12100.2
[8]	xgb_val-mae:11890.9
[9]	xgb_val-mae:11699.4
[0]	xgb_val-mae:14692.7
[1]	xgb_val-mae:13926.1
[2]	xgb_val-mae:13297.7
[3]	xgb_val-mae:12998.9
[4]	xgb_val-mae:12925.9
[5]	xgb_val-mae:13003.5
[6]	xgb_val-mae:13158
[7]	xgb_val-mae:12873.3
[8]	xgb_val-mae:12638.4
[9]	xgb_val-mae:12403.2


In [127]:
#Validation score
np.mean(res)

70.383208002659302

In [132]:
xgb_train = xgb.DMatrix(X_train_1.values, label=y_train)
xgb_val = xgb.DMatrix(X_test_1.values, label=y_test)
    
params = {
    'eta': 0.1, 
    'seed': 42, 
    'subsample': 0.7, 
    'colsample_bytree': 0.7,
    'objective': 'reg:linear', 
    'reg_lambda':0.7,
    'max_depth': 8, 
    'eval_metric': 'mae' 
    }

eval_matrix = [(xgb_val, 'xgb_val')]

final_gb = xgb.train(params, xgb_train, evals = eval_matrix,verbose_eval=1)
    
dtest = xgb.DMatrix(X_test_1.values)
y_xgb_2 = final_gb.predict(dtest)

res_test = smape_fast(y_test.values,y_xgb_2)
    

[0]	xgb_val-mae:10434.8
[1]	xgb_val-mae:9960.08
[2]	xgb_val-mae:9357.29
[3]	xgb_val-mae:8872.79
[4]	xgb_val-mae:8505.66
[5]	xgb_val-mae:8181.5
[6]	xgb_val-mae:7925.89
[7]	xgb_val-mae:7665.17
[8]	xgb_val-mae:7416.5
[9]	xgb_val-mae:7212.87


In [133]:
#test score
res_test

73.299979418624744

## French house insurance prediction (MAPE metric)

**1.** Take a look carefuly at train and test dataset. Note for you what is the difference in them and how they are dependent. You may use any tool you like, any EDA you want. Decribe your validation and reason for your choice in google form.

**2.** 
+ Implement your validation. 
+ Generate additional features. 
+ Build a model you like/you can. 
+ Wait for training your model. If it takes too much time, listen to https://www.youtube.com/watch?v=XWkGL4eZR3E
+ Submit your scores on validation and test to google form. Use MAPE metric for scoring. 
+ Ланфрен ланфра лантатита

In [3]:
train = pd.read_csv('../data/train_french.csv')
test = pd.read_csv('../data/test_french.csv')

In [4]:
train.head()

code_postal  nb_pieces veranda  biens_nomades     sit_fam  \
0        62510          1     NON            500  Indivividu   
1        83126          2     NON            500  Indivividu   
2        68224          3     NON            500  Indivividu   
3        30263          3     NON            500     Famille   
4        72231          2     NON            500     Famille   

                         profession        nature_lri  societe  \
0                    agent; employe  Sans information        2   
1                  cadre; ingenieur  Sans information        2   
2  enseignant; formateur; chercheur            Maison        1   
3                    agent; employe            Maison        2   
4    educateur; animateur; moniteur       Appartement        1   

   domaine_activite niv_urbanisation      ...        var3  var4  var5  var6  \
0                34                A      ...           0   194    49     0   
1                37                A      ...           0     0   100     0   
2                 1                E      ...           1    98   100     0   
3                34                A      ...           0   151    38     0   
4                19                D      ...           0    39   100     0   

   var7  var8  var9  var10  var11  prime_tot_ttc  
0     0     1   NON     30      2          67.68  
1     0     5   NON     12      1         120.60  
2     0     5   NON     30      2         100.62  
3     0     1   NON     15      1          58.73  
4     0     1   NON      0      2         132.65  

[5 rows x 29 columns]

In [38]:
pp.ProfileReport(train)


In [39]:
pp.ProfileReport(test)



In [5]:
train = pd.get_dummies(train, columns = ['var9','veranda','sit_fam','nature_lri','profession','niv_urbanisation'])

In [6]:
test = pd.get_dummies(test, columns = ['var9','veranda','sit_fam','nature_lri','profession','niv_urbanisation'])

In [7]:
y_train = train.prime_tot_ttc
y_test = test.prime_tot_ttc

X_train = train.drop(['code_postal','prime_tot_ttc'],axis = 1)
X_test = test.drop(['code_postal','prime_tot_ttc'],axis = 1)

In [32]:
import math 

def mape_fast(y_true, y_pred):
    out = 0
    for i in range(y_true.shape[0]):
        a = y_true[i]
        b = y_pred[i]
        if b < 1:
            b = 0
        if a == 0:
            continue
        out += math.fabs(a - b) / math.fabs(a)
    out *= (100.0 / y_true.shape[0])
    return out




In [25]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
import xgboost as xgb

regressor = xgb.XGBRegressor(seed = 42, objective = 'reg:linear', subsample = 0.7, colsample_bytree = 0.7,max_depth = 8, n_estimators = 200, learning_rate = 0.1)

pipeline_r = Pipeline([('regressor', regressor)])
param_grid = { 'regressor__reg_lambda': [0.7,0.8,0.9]}
grid_search = GridSearchCV(pipeline_r, param_grid=param_grid, cv=5,scoring = 'neg_mean_absolute_error',verbose = 3, n_jobs = 3)



In [26]:
grid_search.fit(X_train,y_train)


Fitting 5 folds for each of 3 candidates, totalling 15 fits
[CV] regressor__reg_lambda=0.7 .......................................
[CV] regressor__reg_lambda=0.7 .......................................
[CV] regressor__reg_lambda=0.7 .......................................
[CV] ...... regressor__reg_lambda=0.7, score=-15.956156, total= 3.3min
[CV] regressor__reg_lambda=0.7 .......................................
[CV] ...... regressor__reg_lambda=0.7, score=-15.982225, total= 3.3min
[CV] regressor__reg_lambda=0.7 .......................................
[CV] ...... regressor__reg_lambda=0.7, score=-15.843547, total= 3.3min
[CV] regressor__reg_lambda=0.8 .......................................
[CV] ...... regressor__reg_lambda=0.7, score=-15.811364, total= 3.2min
[CV] regressor__reg_lambda=0.8 .......................................
[CV] ...... regressor__reg_lambda=0.7, score=-15.833728, total= 3.2min
[CV] regressor__reg_lambda=0.8 .......................................
[CV] ...... regre

[Parallel(n_jobs=3)]: Done  15 out of  15 | elapsed: 16.6min finished


GridSearchCV(cv=5, error_score='raise',
       estimator=Pipeline(steps=[('regressor', XGBRegressor(base_score=0.5, colsample_bylevel=1, colsample_bytree=0.7,
       gamma=0, learning_rate=0.1, max_delta_step=0, max_depth=8,
       min_child_weight=1, missing=None, n_estimators=200, nthread=-1,
       objective='reg:linear', reg_alpha=0, reg_lambda=1,
       scale_pos_weight=1, seed=42, silent=True, subsample=0.7))]),
       fit_params={}, iid=True, n_jobs=3,
       param_grid={'regressor__reg_lambda': [0.7, 0.8, 0.9]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score=True,
       scoring='neg_mean_absolute_error', verbose=3)

In [27]:
grid_search.best_params_

{'regressor__reg_lambda': 0.7}

In [28]:
y_pred = grid_search.predict(X_test)

In [33]:
mape_fast(y_test.values,y_pred)

17.153648900454